In [1]:
import pdbfixer
import prody
import numpy as np
import py3Dmol
import qrotate


# 1: fetch protein PDB, remove heteroatoms and select ligand

In [2]:
fname = prody.fetchPDB('5WIU', folder='./data/')
pdb = prody.parsePDB(fname)
prody.showProtein(pdb)


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [3]:
protein = pdb.select('protein and chain A')
print(f'Protein atoms: {protein.numAtoms()}')

#nemonapride has resname AQD 
ligand = pdb.select('resname AQD and chain A')
print(f'Ligand atoms: {ligand.numAtoms()}')

Protein atoms: 2736
Ligand atoms: 27


# 2: Align both to the ligand's principal moment of inertia

This minimizes the volume of the search box for docking (assuming you are specifying the search box using a ligand.)

In [4]:
#get coordinates of protein or ligand:
prot_xyz = protein.getCoords()
lig_xyz = ligand.getCoords()

#centre both on the COM of the ligand:
prot_xyz -= lig_xyz.mean(0)
lig_xyz -= lig_xyz.mean(0)

#rotate both so that ligand lies along it's principal axes:
al = qrotate.Align()
angles = al.align_pcl(lig_xyz, get_angles=True)
#apply the rotation matrices:
prot_xyz = prot_xyz.dot(angles[0]).dot(angles[1])
lig_xyz = lig_xyz.dot(angles[0]).dot(angles[1])

protein.setCoords(prot_xyz)
ligand.setCoords(lig_xyz)

prody.writePDB('./data/ligand.pdb', ligand, )
prody.writePDB('./data/protein.pdb', protein,)

'./data/protein.pdb'

# 3: Add missing residues, missing atoms (incl. hydrogens), and minimize hydrogen coords

In this case, we set all non-hydrogen atoms to have zero mass, such that they are ignored by the minimizer. 

Alternatively, one could add positional constraints to the non-hydrogen atoms, giving them some flexibility to move but maintaining overall structure. 

In [5]:
from simtk.openmm import app
from simtk import openmm
from simtk import unit
import pdbfixer


fixer = pdbfixer.PDBFixer('./data/protein.pdb')
fixer.findMissingResidues()
fixer.findMissingAtoms()
fixer.addMissingAtoms()
fixer.addMissingHydrogens(7.0)

In [6]:
forcefield = app.ForceField('amber14-all.xml', 'amber14/tip3pfb.xml')

system = forcefield.createSystem(fixer.topology, nonbondedMethod=app.CutoffNonPeriodic,
         nonbondedCutoff=0.9*unit.nanometer)


atom_elements = [atom.element.name for atom in fixer.topology.atoms()]
for i in range(system.getNumParticles()):
    if atom_elements[i]!='hydrogen':
        system.setParticleMass( i, 0.0 )
        
        
##constraints alternative:
##don't use this as well as setting masses to zeros- it's one or the other
# constraint_force = openmm.CustomExternalForce('k*((x-x0)^2+(y-y0)^2+(z-z0)^2)')
# constraint_force.addGlobalParameter("k", 50*unit.kilocalorie_per_mole); #reduce this number to give more flexibility
# constraint_force.addPerParticleParameter("x0");
# constraint_force.addPerParticleParameter("y0");
# constraint_force.addPerParticleParameter("z0");

# atom_elements = [atom.element.name for atom in fixer.topology.atoms()]
# for i in range(system.getNumParticles()):
#     if atom_elements[i]!='hydrogen':
#         constraint_force.addParticle(i, fixer.positions[i])
# system.addForce(constraint_force)


In [7]:
integrator = openmm.LangevinIntegrator(298*unit.kelvin, 1/unit.picosecond, 1*unit.femtosecond)
platform = openmm.Platform.getPlatformByName('CPU')

simulation = app.Simulation(fixer.topology, system, integrator, platform)
simulation.context.setPositions(fixer.positions)
simulation.minimizeEnergy()

In [8]:
positions = simulation.context.getState(getPositions=True).getPositions()

app.PDBFile.writeFile(fixer.topology, positions, open('./data/proteinH.pdb', 'w'))


In [9]:
view = py3Dmol.view()

view.addModel(open('./data/protein.pdb').read(), 'pdb')
view.addStyle({'model':0}, {'stick':{'colorscheme':'orangeCarbon', 'radius':0.1}})

view.addModel(open('./data/proteinH.pdb').read(), 'pdb')
view.addStyle({'model':1}, {'stick':{'colorscheme':'blueCarbon', 'radius':0.1}})

view.addModel(open('./data/ligand.pdb').read(), 'pdb')
view.addStyle({'model':2}, {'stick':{'colorscheme':'greenCarbon'}})

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

# 4: (optional): parameterize ligand with GAFF, and minimize binding site coordinates 

Things get messier here but this step is usually not necessary for docking. 


In [10]:
from rdkit import Chem
from rdkit.Chem import AllChem
import parmed as pmd
from openff.toolkit.topology import Molecule
from openmmforcefields.generators import GAFFTemplateGenerator


In [11]:

lig_smiles = 'C[C@@H]1[C@@H](CCN1Cc2ccccc2)NC(=O)c3cc(c(cc3OC)NC)Cl'
lig_mol_ref = Chem.MolFromSmiles(lig_smiles)
lig_mol_pdb = Chem.MolFromPDBFile('./data/ligand.pdb')
lig_mol_pdb = AllChem.AssignBondOrdersFromTemplate(lig_mol_ref, lig_mol_pdb)
lig_mol_pdb = Chem.AddHs(lig_mol_pdb, addCoords=True)


#set all the PDB properties. 
#the main thing here is the residue name becomes 'UNL'
#which is always the same in simulations - and it is what 
#we want openforcefield to use as the residue name for a bound ligand. 
#This is not necesssary, it's just how I do it. 
elem_count = {}
for a in lig_mol_pdb.GetAtoms():
    n = elem_count.get(a.GetAtomicNum(), 0)
    n += 1
    elem_count[a.GetAtomicNum()] = n
    n = min(n, 99)
    mi = Chem.AtomPDBResidueInfo()
    mi.SetResidueName('UNL')
    mi.SetChainId('A')
    mi.SetResidueNumber(1)
    atom_name = '{0:>2s}{1:<2d}'.format(a.GetSymbol(), n)
    mi.SetIsHeteroAtom(True)
    mi.SetName(atom_name)
    mi.SetOccupancy(0.0)
    mi.SetTempFactor(0.0)
    a.SetMonomerInfo(mi)

    
Chem.MolToPDBFile(lig_mol_pdb, './data/ligandH.pdb')

In [12]:
protein_pmd = pmd.load_file('./data/proteinH.pdb')
ligand_pmd = pmd.load_file('./data/ligandH.pdb')

combined = protein_pmd + ligand_pmd
combined.save('./data/combined.pdb',overwrite=True)


In [13]:
# Create an OpenFF Molecule object for benzene from SMILES
molecule = Molecule.from_rdkit(lig_mol_pdb)
# Create the GAFF template generator
gaff = GAFFTemplateGenerator(molecules=molecule)

# Create an OpenMM ForceField object with AMBER ff14SB
forcefield = app.ForceField('amber/protein.ff14SB.xml', 'amber/tip3p_standard.xml')
# Register the GAFF template generator
forcefield.registerTemplateGenerator(gaff.generator)
# You can now parameterize an OpenMM Topology object that contains the specified molecule.
# forcefield will load the appropriate GAFF parameters when needed, and antechamber
# will be used to generate small molecule parameters on the fly.


In [14]:
#instantiate a Modeller object using the topology and xyz coordinates,
lig_pdb = app.PDBFile('./data/ligandH.pdb')
lig_system = forcefield.createSystem(lig_pdb.topology, nonbondedMethod=app.CutoffNonPeriodic,
         nonbondedCutoff=0.9*unit.nanometer)
prot_pdb = app.PDBFile('./data/proteinH.pdb')
prot_system = forcefield.createSystem(prot_pdb.topology, nonbondedMethod=app.CutoffNonPeriodic,
         nonbondedCutoff=0.9*unit.nanometer)


In [15]:
#join the systems with parmed:
lig_structure = pmd.openmm.load_topology(lig_pdb.topology,
                                           lig_system,
                                           xyz=lig_pdb.positions)
prot_structure = pmd.openmm.load_topology(prot_pdb.topology,
                                           prot_system,
                                           xyz=prot_pdb.positions)
complex_structure = lig_structure + prot_structure


In [16]:
#### With added solvent molecules:

# modeller = app.Modeller(complex_structure.topology, complex_structure.positions)
# modeller.addSolvent(forcefield, 
#                      model='tip3p',
#                     #0.15*unit.molar, 
#                     padding=1*unit.nanometer, )


# ###With solvent:

# complex_system = forcefield.createSystem(modeller.topology, nonbondedMethod=app.PME,
#          nonbondedCutoff=0.9*unit.nanometer, constraints=app.HBonds)
# for c, f in enumerate(complex_system.getForces()):
#     f.setForceGroup(c)
#     if isinstance(f, openmm.NonbondedForce):
#         print('nonbonded is:', c)

# integrator = openmm.LangevinIntegrator(298*unit.kelvin, 1/unit.picosecond, 1*unit.femtosecond)
# platform = openmm.Platform.getPlatformByName('OpenCL')

# simulation = app.Simulation(modeller.topology, complex_system, integrator, platform)
# simulation.context.setPositions(modeller.positions)


In [17]:
#### Without solvent:

# Convert the Structure to an OpenMM System in vacuum.
complex_system = complex_structure.createSystem(nonbondedMethod=app.CutoffNonPeriodic,
                                                nonbondedCutoff=9.0*unit.angstrom,
                                                removeCMMotion=False)

#for count, at in enumerate(complex_structure.atoms):
#    if at.atomic_number>1:
#        complex_system.setParticleMass(count, 0) #set nonhydrogen atoms to zero mass - they won't move. 
        
        
    
integrator = openmm.LangevinIntegrator(298*unit.kelvin, 1/unit.picosecond, 1*unit.femtosecond)
platform = openmm.Platform.getPlatformByName('OpenCL')

simulation = app.Simulation(complex_structure.topology, complex_system, integrator, platform)
simulation.context.setPositions(complex_structure.positions)

In [18]:
simulation.minimizeEnergy()

In [19]:
app.PDBFile.writeFile(complex_structure.topology,
                  simulation.context.getState(getPositions=True).getPositions(),
                  open('./data/gaff_minimized.pdb', 'w') )

In [20]:
view = py3Dmol.view()

view.addModel(open('./data/gaff_minimized.pdb').read(), 'pdb')
view.addStyle({'model':0}, {'stick':{'colorscheme':'orangeCarbon', 'radius':0.1}})

#compare to original coordinates:
view.addModel(open('./data/proteinH.pdb').read(), 'pdb')
view.addStyle({'model':1}, {'stick':{'colorscheme':'blueCarbon', 'radius':0.1}})

#compare ligand to original coordinates:
view.addModel(open('./data/ligand.pdb').read(), 'pdb')
view.addStyle({'model':2}, {'stick':{'colorscheme':'greenCarbon'}})

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol